## This is the example code for loading the data in Wang et al.(2023) "Projection of future fire emissions over the contiguous US using explainable artificial intelligence and CMIP6 models" and training the neural network model

In [1]:
import os
import numpy as np
import pandas as pd
import torch

In [2]:
from tqdm import tqdm
import seaborn as sns
from pylab import rcParams
import matplotlib.pyplot as plt
from matplotlib import rc
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, classification_report

/Users/wang112/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [3]:
from torch import nn, optim
import torch.nn.functional as F


In [4]:
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
torch.manual_seed(RANDOM_SEED)

In [5]:
# import data
import os

#os.environ['R_HOME'] = '/Users/wang112/opt/anaconda3/envs/py37/lib/R'

import rpy2.robjects as robjects
from rpy2.robjects import pandas2ri
import numpy as np
pandas2ri.activate()

import os
os.chdir('/Users/wang112/Documents/fire_projection_202122/paper/share_data/')

readRDS = robjects.r['readRDS']
df_fire_emission = readRDS('ten_fold_NN_reanalysis_predictors_results_200020_v2.rds')


In [6]:
print(df_fire_emission)

             rhum      apcp    Lon   Lat  Year  Month  fire_PM25_emissions  \
1       47.491837  1.375767 -102.5  40.5  2015      7             0.000035   
2       40.120383  0.093586 -103.5  35.5  2008     11             0.000024   
3       62.950172  0.557636  -93.5  39.5  2000      4             0.015366   
4       79.612932  0.494990 -108.5  36.5  2020      1             0.000036   
5       68.925379  3.770687  -84.5  36.5  2007      4             0.004843   
...           ...       ...    ...   ...   ...    ...                  ...   
227804  76.627555  0.868347  -88.5  43.5  2000     10             0.000002   
227805  44.900995  1.186431 -115.5  42.5  2015      4             0.000270   
227806  75.170218  3.378964  -91.5  29.5  2001      8             0.001590   
227807  11.029052  0.000609 -116.5  35.5  2018      6             0.000529   
227808  47.902346  1.528344 -106.5  40.5  2005      9             0.001542   

            SPEI     wndsp       VPD  ...  shrub          crop 

In [7]:
X = df_fire_emission[['rhum','apcp','Lon','Lat','Year',"Month",'fire_PM25_emissions', \
        'SPEI','wndsp','VPD','soilm','LAI','veg_frac','pop','SVD1_NCA','SVD2_NCA',\
       'SVD1_RM','SVD2_RM','SVD1_SElag2','SVD2_SElag2','grass','shrub','crop','nonveg','tree','resid','nor.temp',\
        'nor.rhum','nor.apcp','nor.VPD']]
y = df_fire_emission[['fire_PM25_emissions']]

In [8]:
# Train - Test
X_trainval, X_test, y_trainval, y_test = train_test_split(X, y, test_size=0.1, random_state=69)
# Split train into train-val
X_train, X_val, y_train, y_val = train_test_split(X_trainval, y_trainval, test_size=0.1, random_state=21)

In [9]:
# remove the label
X_train2 = X_train.drop(['Lon','Lat','Year','Month','fire_PM25_emissions'], axis=1)
X_val2 = X_val.drop(['Lon','Lat','Year','Month','fire_PM25_emissions'], axis=1)  
X_test2 = X_test.drop(['Lon','Lat','Year','Month','fire_PM25_emissions'], axis=1)  

In [10]:
from sklearn.preprocessing import MinMaxScaler

sc = MinMaxScaler()

X_train3 = sc.fit_transform(X_train2)
X_val3 = sc.transform(X_val2)
X_test3 = sc.transform(X_test2)

# scale target variable

y_train = np.array(y_train)
y_val = np.array(y_val)
y_test = np.array(y_test)



In [11]:
from torch.utils.data import Dataset, DataLoader

class RegressionDataset(Dataset):
    
    def __init__(self, X_data, y_data):
        self.X_data = X_data
        self.y_data = y_data
        
    def __getitem__(self, index):
        return self.X_data[index], self.y_data[index]
        
    def __len__ (self):
        return len(self.X_data)
    
train_dataset = RegressionDataset(torch.from_numpy(X_train3).float(), torch.from_numpy(y_train).float())
val_dataset = RegressionDataset(torch.from_numpy(X_val3).float(), torch.from_numpy(y_val).float())
test_dataset = RegressionDataset(torch.from_numpy(X_test3).float(), torch.from_numpy(y_test).float())

In [12]:
EPOCHS = 200
BATCH_SIZE = 64

In [13]:
train_loader = DataLoader(dataset=train_dataset, batch_size=BATCH_SIZE) #, shuffle=True
val_loader = DataLoader(dataset=val_dataset, batch_size=1)
test_loader = DataLoader(dataset=test_dataset, batch_size=1)

In [14]:
class Net(nn.Module):
    def __init__(self, n_features):
        super(Net, self).__init__()
#        self._to_linear = None    
        self.layer_1 = nn.Linear(n_features,200)
        nn.init.kaiming_normal_(self.layer_1.weight)
        self.layer_2 = nn.Linear(200, 150)
        nn.init.kaiming_normal_(self.layer_2.weight)
        self.layer_3 = nn.Linear(150, 80)
        nn.init.kaiming_normal_(self.layer_3.weight)
        self.layer_out = nn.Linear(80, 1)
        nn.init.kaiming_normal_(self.layer_out.weight)

        # define relu
        self.relu = nn.ReLU()


    
    def forward(self, inputs):
        x = self.relu(self.layer_1(inputs))
        x = self.relu(self.layer_2(x))
        x = self.relu(self.layer_3(x))
        x = self.layer_out(x)
        return (x)

    


In [15]:
net = Net(X_train3.shape[1])
print(net)

Net(
  (layer_1): Linear(in_features=25, out_features=200, bias=True)
  (layer_2): Linear(in_features=200, out_features=150, bias=True)
  (layer_3): Linear(in_features=150, out_features=80, bias=True)
  (layer_out): Linear(in_features=80, out_features=1, bias=True)
  (relu): ReLU()
)


In [16]:
l = nn.MSELoss()

In [17]:
optimizer = optim.SGD(net.parameters(), lr=0.01)

In [18]:
from scipy.stats import pearsonr

loss_stats = {
    'train': [],
    "val": []
}

torch.manual_seed(RANDOM_SEED)

In [19]:
print("Begin training.")
for e in tqdm(range(1, EPOCHS+1)):
    score = []
    # TRAINING
    train_epoch_loss = 0
    net.train()
    for X_train_batch, y_train_batch in train_loader:
        
        # reset gradients to zero
        optimizer.zero_grad()
        
        # generate prediction
        y_train_pred = net(X_train_batch)
        # calculate loss
        train_loss = l(y_train_pred, y_train_batch)
        
        Before = list(net.parameters())[0].clone()
        # compute gradients
        train_loss.backward()




        # update parameters using gradients
        optimizer.step()
        After = list(net.parameters())[0].clone()
        
        train_epoch_loss += train_loss.item()
        
    
        
        
    # VALIDATION    
    with torch.no_grad():
        val_epoch_loss = 0
        
        net.eval()
        for X_val_batch, y_val_batch in val_loader:
            
            y_val_pred = net(X_val_batch)
                        
            val_loss = l(y_val_pred, y_val_batch)
            
            val_epoch_loss += val_loss.item()
    
    print(f'Epoch {e+0:03}: | Train Loss: {train_epoch_loss/len(train_loader):.5f} | Val Loss: {val_epoch_loss/len(val_loader):.5f}')






  0%|          | 0/200 [00:00<?, ?it/s]

Begin training.


  0%|          | 1/200 [00:06<21:54,  6.60s/it]

Epoch 001: | Train Loss: 0.01058 | Val Loss: 0.02465


  1%|          | 2/200 [00:13<21:50,  6.62s/it]

...

Epoch 198: | Train Loss: 0.00621 | Val Loss: 0.01889


100%|█████████▉| 199/200 [22:15<00:06,  6.49s/it]

Epoch 199: | Train Loss: 0.00620 | Val Loss: 0.01885


100%|██████████| 200/200 [22:22<00:00,  6.71s/it]

Epoch 200: | Train Loss: 0.00618 | Val Loss: 0.01882


In [20]:
y_pred_list = []
with torch.no_grad():
    net.eval()
    for X_batch, _ in test_loader:
        X_batch = X_batch#.to(device)
        y_test_pred = net(X_batch)
        y_pred_list.append(y_test_pred.cpu().numpy())
y_pred_list = [a.squeeze().tolist() for a in y_pred_list]


In [21]:
from sklearn.metrics import mean_squared_error, r2_score
import math

mse = mean_squared_error(y_test, y_pred_list)
print("Mean Squared Error :",mse)


Mean Squared Error : 0.004555346025939337
